In [168]:
## loading checkpoint files

%load_ext autoreload
%autoreload 2

from analysis.utils import *
from analysis.parse import *
from analysis.analy import *
from analysis.graphs import *

# ==== LOAD DREAMCODER
ECTRAIN = "S12.10.test4"
DAT = loadCheckpoint(trainset=ECTRAIN, loadparse=False, loadbehavior=False)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
experimentOutputs/draw/2019-11-10T22:47:09.031267/draw_aic=1.0_arity=2_BO=True_CO=True_dp=True_doshaping=False_ES=1_ET=10_HR=0.5_it=15_MF=5_noConsol=False_parallelTest=True_pc=30_RT=2400_RR=False_RW=False_st=False_solver=ocaml_STM=True_L=1.5_TRR=unsolved_K=2_topkNotMAP=False_tset=S12.pickle
0
----
experimentOutputs/draw/2019-11-10T22:47:09.031267/draw_aic=1.0_arity=2_BO=True_CO=True_dp=True_doshaping=False_ES=1_ET=10_HR=0.5_it=16_MF=5_noConsol=False_parallelTest=True_pc=30_RT=2400_RR=False_RW=False_st=False_solver=ocaml_STM=True_L=1.5_TRR=unsolved_K=2_topkNotMAP=False_tset=S12_graph=True.pickle
16
----
experimentOutputs/draw/2019-11-10T22:47:09.031267/draw_aic=1.0_arity=2_BO=True_CO=True_dp=True_doshaping=False_ES=1_ET=10_HR=0.5_it=15_MF=5_noConsol=False_parallelTest=True_pc=30_RT=2400_RR=False_RW=False_st=False_solver=ocaml_STM=True_L=1.5_TRR=unsolved_K=2_topkNotMAP=False_tset=S12_graph=True.pickle

In [169]:
# === 4) Load tools to work with tasks libraries
%load_ext autoreload
%autoreload 2

from analysis.utils import *
from analysis.parse import *
from analysis.analy import *
from analysis.graphs import *
import dreamcoder.domains.draw.primitives as P

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [170]:
from dreamcoder.domains.draw import drawPrimitives as DP

In [171]:
# GET PRIMITIVES TO RENAME
p_to_ignore = ['line', 'circle', 'transmat', 'transform', 
               'reflect', 'connect', 'repeat', "None", "Some"]
               
primcodes = {p.name:p.evaluate([]) for p in DP.primitives[::-1] if p.name not in p_to_ignore}
primcodes["None"]="N"
primcodes["Some"]=''
primcodes = {key:str(value)[:5] for key, value in primcodes.items()}

if ECTRAIN in ["S12.10.test4", "S13.10.test4"]:
    primcodes.update({
        "#(lambda (lambda (transmat N N $0 ( 0.28) $1)))":"#[MOVE X $ AND UP 0.28]",
        "#(lambda (transmat N N ( $0) N N))":"#[MOVE X $0]",
        "#(transform line (transmat ( 4.0) ( 1.570) ( -1.75) ( -2.0) N))":"#[VERTLINE LEFT]",
        "#(transform line (#[MOVE X $0] -0.5))":"#[HORIZLINE]",
        "#(lambda (lambda (transform (repeat $0 $1 (#[MOVE X $0] 1.1)) (#[MOVE X $0] -1.75))))":"#[PRIM $ REPEAT TO RIGHT]",
        "#(lambda (repeat #[VERTLINE LEFT] $0 (#[MOVE X $0] 1.1)))":"#[GRATING]",
        "#(lambda (transform (#[PRIM $ REPEAT TO RIGHT] $0 line) (#[MOVE X $0] -0.5)))":"#[HLINE REP RIGHT $]",
        "#(transform #[HORIZLINE] (#[MOVE X $0] -0.65))":"#[HLINE at -0.65]",
        "#(lambda (lambda (transmat N N $0 ( 1.0) $1)))":"#[MOVE X $ and Y 1]",
        "#(repeat #[HLINE at -0.65] 2)":"#[REPEAT 2 HLINE LEFT]",
        "#(lambda (lambda (connect (transform circle (#[MOVE X $ and Y 1] ( $0) ( $1))))))":"#[CIRCLE X$ Y1 + P$]",
        "#(lambda (lambda (connect (#[GRATING] $0) (reflect $1 0.0))))":"#[GRATING + REFLECT P$ 0]",
        "#(#[CIRCLE X$ Y1 + P$] -0.65)":"#[CIRCLE -0.65 1 + P$]",
        "#(lambda (lambda (#[CIRCLE X$ Y1 + P$] -1.75 $0 (reflect $1 0.0))))":"#[CIRCLE -1.75,1 + P$]",
        "#(lambda (lambda (#[GRATING + REFLECT P$ 0] (#[CIRCLE X$ Y1 + P$] 1.55 $1 $0) 4)))":"#[GRATING + CIRCLE 1.55,-1 + P$]",
        "#(lambda (lambda (connect (#[PRIM $ REPEAT TO RIGHT] 1 (connect (transform #[HORIZLINE] (transmat N N N ( 1.0) $0)) circle)) (#[GRATING] $1))))":"#[GRATING + LINE + CIRCLE]",
        "#(#[CIRCLE X$ Y1 + P$] 0.45 trs)":"#[CIRCLE + $]",
        "#(lambda (transform line (transmat ( $0) ( 1.570) ( -1.75) ( -2.0) N)))":"#[VLINE $S at -1.75,-2]",
        "#(#(lambda (lambda (connect (transform $0 (transmat N N $1 ( -1.0) N))))) ( -1.75) circle)":"#[CIRCLE -1.75, -1]",
        "#(lambda (lambda (repeat (#[VLINE $S at -1.75,-2] $1) $0 (#[MOVE X $0] 1.1))))":"#[REP VLINE $S -1.75,-2 by X 1.1 $R]",
        "#(connect (transform circle (#[MOVE X $0] -1.75)))":"#[CIRCLE + $P -1.75,0]",
        "#(lambda (lambda (connect (transform $0 (transmat N N $1 ( -1.0) N)))))":"#[$P $X -1]",
        "#(lambda (lambda (connect $1 (transform $0 (#[MOVE X $0] 1.1)))))":"#[$P + $P at X1.1]",
        "#(lambda (lambda (#[$P + $P at X1.1] (#[REP VLINE $S -1.75,-2 by X 1.1 $R] $1 4) (#[CIRCLE + $P -1.75,0] $0))))":"#[$P + $P at X1.1 + 4GRATING, variable height + CIRCLE at -1.75,0]",
        "#(lambda (lambda (connect (transform $0 (transmat None None $1 (Some dist3) None)))))":"#[$P -1X]",
        "#(lambda (lambda (connect $1 (transform $0 (#(lambda (transmat None None (Some $0) None None)) dist18)))))":"#[$P + $P moved X1.1]",
        "#(transform (#(lambda (transform (repeat (transform line (#[MOVE X $0] -1.75)) $0 (#[MOVE X $0] 1.1)) (#[MOVE X $0] -0.5))) 1) (#[MOVE X $0] 1.1))":"[REP HLINE MOVE START -1.75 BY X1.1 + $P at X-0.5 and $P at X1.1]"
    })


In [163]:
# note will do in order from top to bottom
result=DAT["result"]

# ==== go thru all primitives and replace if possible
P = result.grammars[-1].primitives
for i, p in enumerate(P):
    pp = str(p)
    print(i)
    print(pp)
    print( )
    for key in primcodes.keys():
        pp = pp.replace(key, primcodes[key])
    print(pp)
    print('-------')

0
#(lambda (reflect (#(lambda (#(#(lambda (lambda (connect (transform $0 (transmat None None $1 (Some dist3) None))))) (Some dist14) circle) (#(lambda (lambda (connect (transform $0 (transmat None None $1 (Some dist3) None))))) None (#(lambda (lambda (transform (connect (#(lambda (transform (repeat (transform line (#(lambda (transmat None None (Some $0) None None)) dist14)) $0 (#(lambda (transmat None None (Some $0) None None)) dist18)) (#(lambda (transmat None None (Some $0) None None)) dist4))) $0) (transform circle (#(lambda (transmat None None (Some $0) None None)) $1)))))) dist16 rep1 (#(lambda (transmat None None (Some $0) None None)) dist18)) $0))) $0) angle0))

#(lambda (reflect (#(lambda (#[CIRCLE -1.75, -1] (#[$P $X -1] N (#(lambda (lambda (transform (connect (#(lambda (transform (repeat (transform line (#[MOVE X $0] -1.75)) $0 (#[MOVE X $0] 1.1)) (#[MOVE X $0] -0.5))) $0) (transform circle (#[MOVE X $0] $1)))))) 0.45 2 (#[MOVE X $0] 1.1)) $0))) $0) 0.0))
-------
1
#(lambda (

In [166]:
# GO THRU ALL PRIMITIVES
    
    
# --- save
fname = "{}/{}_solutions_simple.txt".format(DAT["summarysavedir"], testortrain)
print(fname)
stringall = []
# ==== go thru all primitives and replace if possible
P = result.grammars[-1].primitives
for i, p in enumerate(P):
    pp = str(p)
       
    stringall.append(i)
    stringall.append(t.name)
    stringall.append(pp)
    stringall.append(" ")
    for key in primcodes.keys():
        pp = pp.replace(key, primcodes[key])
    stringall.append(pp)
    stringall.append('-------')
with open(fname, "w") as f:
    for s in stringall:
        print(s)
        f.write(str(s)+"\n")


analysis/summary/DAT_ecS13.10.test4_dg2.4/train_solutions_simple.txt
0
S13_265
#(lambda (reflect (#(lambda (#(#(lambda (lambda (connect (transform $0 (transmat None None $1 (Some dist3) None))))) (Some dist14) circle) (#(lambda (lambda (connect (transform $0 (transmat None None $1 (Some dist3) None))))) None (#(lambda (lambda (transform (connect (#(lambda (transform (repeat (transform line (#(lambda (transmat None None (Some $0) None None)) dist14)) $0 (#(lambda (transmat None None (Some $0) None None)) dist18)) (#(lambda (transmat None None (Some $0) None None)) dist4))) $0) (transform circle (#(lambda (transmat None None (Some $0) None None)) $1)))))) dist16 rep1 (#(lambda (transmat None None (Some $0) None None)) dist18)) $0))) $0) angle0))
 
#(lambda (reflect (#(lambda (#[CIRCLE -1.75, -1] (#[$P $X -1] N (#(lambda (lambda (transform (connect (#(lambda (transform (repeat (transform line (#[MOVE X $0] -1.75)) $0 (#[MOVE X $0] 1.1)) (#[MOVE X $0] -0.5))) $0) (transform circle (#[MOVE 

In [165]:
# GO THRU ALL SOLUTIONS
# for stim in stimlist:
#     t = DATgetTask(stim, DAT)
#     result.frontiersOverTime(t)[-1]
#     raise
    
testortrain = "train"
if testortrain=="train":
    tasks = DAT["tasks"]
else:
    tasks = DAT["testtasks"]
    
# --- save
fname = "{}/{}_solutions_{}_simple.txt".format(DAT["summarysavedir"], DAT["trainset"], testortrain)
# fname = "/tmp/test.txt"
print(fname)
stringall = []
for i, t in enumerate(tasks):
    if result.frontiersOverTime[t][-1].empty:
        continue
        
    pp = str(result.frontiersOverTime[t][-1].bestPosterior.program)
    
    stringall.append(i)
    stringall.append(t.name)
    stringall.append(pp)
    stringall.append(" ")
    for key in primcodes.keys():
        pp = pp.replace(key, primcodes[key])
    stringall.append(pp)
    stringall.append('-------')
with open(fname, "w") as f:
    for s in stringall:
        print(s)
        f.write(str(s)+"\n")


analysis/summary/DAT_ecS13.10.test4_dg2.4/S13.10.test4_solutions_train_simple.txt
0
S12_13_shaping_0
(#(lambda (transform line (transmat (Some $0) (Some angle2) (Some dist14) (Some dist1) None))) scale7)
 
(#[VLINE $S at -1.75,-2] 4.0)
-------
1
S12_13_shaping_1
(#(lambda (lambda (repeat (#(lambda (transform line (transmat (Some $0) (Some angle2) (Some dist14) (Some dist1) None))) $1) $0 (#(lambda (transmat None None (Some $0) None None)) dist18)))) scale7 rep1)
 
(#[REP VLINE $S -1.75,-2 by X 1.1 $R] 4.0 2)
-------
2
S12_13_shaping_2
(#(lambda (lambda (repeat (#(lambda (transform line (transmat (Some $0) (Some angle2) (Some dist14) (Some dist1) None))) $1) $0 (#(lambda (transmat None None (Some $0) None None)) dist18)))) scale7 rep2)
 
(#[REP VLINE $S -1.75,-2 by X 1.1 $R] 4.0 3)
-------
3
S12_13_shaping_3
(#(lambda (lambda (repeat (#(lambda (transform line (transmat (Some $0) (Some angle2) (Some dist14) (Some dist1) None))) $1) $0 (#(lambda (transmat None None (Some $0) None None)) d

-------


In [95]:
result.frontiersOverTime

{Task(name=S12_13_test_1, request=tstroke, examples=[]: [Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[], task=S12_13_test_1),
  Frontier(entries=[FrontierEntry(program=(#(lambda (lambda (#(lambda (lambda (connect (#(lambda (repeat #(transform line (transmat (Some scale7) (Some angle2) (Some dist14) (Some dist1) None)) $0 (#(lambda (transmat None None (Some $0) None None)) dist18))) $0) (reflect $1 angle0)))) (#(lambda (lambda (connect (transform circl

In [87]:
DAT.keys()


dict_keys(['trainset', 'result', 'tasks', 'testtasks', 'programnames', 'programnames_test', 'behaviorexpt', 'savedir', 'parses', 'analysavedir', 'summarysavedir', 'loadparse', 'savedir_datsegs', 'datflatsavedir', 'savedir_modelhudist'])